# IMPORTING THE DATA

I downloaded the publicly available data directly from the Inside Airbnb website. It covers all Austin listing details, calendar details, review details and associated geolocation information collected on September 19th, 2019. The data was published in the form of multiple csv files.
<ul>
    <li>Listings.csv - Detailed listings data for Austin</li>
	<li>Calendar.csv - Detailed calendar data for listings in Austin</li>
	<li>Reviews.csv - Detailed reviews data for listings in Austin</li>
	<li>Neighbourhoods.geojson - GeoJSON file of neighbourhoods of the city</li>
</ul>
I will use Python to import the csv files into my Jupyter notebook to clean and explore the data. 

In [113]:
# Import required libraries
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from pandas.api.types import is_string_dtype
import re
import seaborn as sns
import cufflinks as cf
import plotly.offline
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

# Read in the csv file
df = pd.read_csv('Data/listings.csv', low_memory=False)

# FEATURE SELECTION
Since there is no data dictionary available, I will familiarize myself with the columns to understand what each feature represents. This will help me to determine which columns I don't need and can remove, as to ensure that the data is used in the most productive and meaningful manner. 

I will inspect the shape of the data to determine how many columns and rows there are.

In [114]:
# Inspect the number of rows and columns
df.shape

(11339, 106)

There are 106 different columns in the listings csv file. I will inspect each and every column to determine which ones will be important for further processing, 20 columns at a time.

In [115]:
# Inspect the first 20 columns and first 5 rows
df.iloc[:5, :20]

id                        listing_url       scrape_id last_scraped  \
0  2265  https://www.airbnb.com/rooms/2265  20190919050302   2019-09-19   
1  5245  https://www.airbnb.com/rooms/5245  20190919050302   2019-09-19   
2  5456  https://www.airbnb.com/rooms/5456  20190919050302   2019-09-19   
3  5769  https://www.airbnb.com/rooms/5769  20190919050302   2019-09-19   
4  6413  https://www.airbnb.com/rooms/6413  20190919050302   2019-09-19   

                                                name  \
0   Zen-East in the Heart of Austin (monthly rental)   
1  Eco friendly, Colorful, Clean, Cozy monthly share   
2          Walk to 6th, Rainey St and Convention Ctr   
3                                     NW Austin Room   
4                      Gem of a Studio near Downtown   

                                                                                               summary  \
0  Zen East is situated in a vibrant & diverse multicultural neighborhood, within walking distance ...   
1  Situated in a vibrant & diverse multicultural neighborhood & within walking distance of many gre...   
2  Fabulous location for walking to Convention Center, Rainey Street, East 6th Street, Downtown, Co...   
3                                                                                                  NaN   
4  Great studio apartment, perfect for couples or singles. Just 1 mile into downtown. Convenient fo...   

                                                                                                 space  \
0  This colorful and clean 1923 house was completely remodeled in 2004. The house is a 2BR/ 2BA (13...   
1  This green, colorful, clean and cozy house was built in 1923 and remodeled in 2004. As the homeo...   
2  Cute Private Studio apartment located in Willow Spence National Historic District.  It is  walki...   
3  Looking for a comfortable inexpensive room to stay for a night?  A week or more?  Join us in our...   
4  (License #114332) Large, contemporary studio apartment available for vacation and short-term cor...   

                                                                                           description  \
0  Zen East is situated in a vibrant & diverse multicultural neighborhood, within walking distance ...   
1  Situated in a vibrant & diverse multicultural neighborhood & within walking distance of many gre...   
2  Fabulous location for walking to Convention Center, Rainey Street, East 6th Street, Downtown, Co...   
3  Looking for a comfortable inexpensive room to stay for a night?  A week or more?  Join us in our...   
4  Great studio apartment, perfect for couples or singles. Just 1 mile into downtown. Convenient fo...   

  experiences_offered  \
0                none   
1                none   
2                none   
3                none   
4                none   

                                                                                 neighborhood_overview  \
0                                                                                                  NaN   
1                                                                                                  NaN   
2  My neighborhood is ideally located if you want to walk to bars and restaurants downtown, East 6t...   
3                                            Quiet neighborhood with lots of trees and good neighbors.   
4  Travis Heights is one of the oldest neighborhoods in Austin. Our house was built in 1937. We reb...   

                                                                                                 notes  \
0  A 2013 Genuine Buddy Scooter 125 may be available to rent for $30 a day.  Two  people (~ 300 lbs...   
1  Please note: A two story studio was built in the backyard in early 2017.  You have a front porch...   
2  Parking on street requires a permit.  There is a $50 deposit to obtain a permit. 15% hotel taxes...   
3                                                                                             

<b>From the first 20 columns, the following will remain</b>
	<ul>
    <li>id - unique identifier that could be used to join other data files</li>
    </ul>

In [116]:
# Inspect the next 20 columns and first 5 rows
df.iloc[:5, 20:40]

host_url  host_name  host_since  \
0   https://www.airbnb.com/users/show/2466      Paddy  2008-08-23   
1   https://www.airbnb.com/users/show/2466      Paddy  2008-08-23   
2   https://www.airbnb.com/users/show/8028     Sylvia  2009-02-16   
3   https://www.airbnb.com/users/show/8186  Elizabeth  2009-02-19   
4  https://www.airbnb.com/users/show/13879       Todd  2009-04-17   

                  host_location  \
0  Austin, Texas, United States   
1  Austin, Texas, United States   
2  Austin, Texas, United States   
3  Austin, Texas, United States   
4  Austin, Texas, United States   

                                                                                            host_about  \
0  I am a long time resident of Austin. I earned a few degrees at UT a few decades ago and practice...   
1  I am a long time resident of Austin. I earned a few degrees at UT a few decades ago and practice...   
2  I am a licensed Real Estate Broker and owner of Armadillo Realty.  I attended The University of ...   
3  We're easygoing professionals that enjoy meeting new people.  I love martial arts, the outdoors,...   
4  We're a young family that likes to travel, we just don't get to enough. So we live vicariously t...   

   host_response_time host_response_rate  host_acceptance_rate  \
0  within a few hours               100%                   NaN   
1  within a few hours               100%                   NaN   
2      within an hour               100%                   NaN   
3      within an hour               100%                   NaN   
4      within an hour               100%                   NaN   

  host_is_superhost  \
0                 t   
1                 t   
2                 t   
3                 t   
4                 t   

                                                                                    host_thumbnail_url  \
0   https://a0.muscache.com/im/users/2466/profile_pic/1259094587/original.jpg?aki_policy=profile_small   
1   https://a0.muscache.com/im/users/2466/profile_pic/1259094587/original.jpg?aki_policy=profile_small   
2   https://a0.muscache.com/im/users/8028/profile_pic/1329882962/original.jpg?aki_policy=profile_small   
3   https://a0.muscache.com/im/users/8186/profile_pic/1272556663/original.jpg?aki_policy=profile_small   
4  https://a0.muscache.com/im/pictures/4f35ef11-7f37-45cf-80da-f914a6d5f451.jpg?aki_policy=profile_...   

                                                                                      host_picture_url  \
0  https://a0.muscache.com/im/users/2466/profile_pic/1259094587/original.jpg?aki_policy=profile_x_m...   
1  https://a0.muscache.com/im/users/2466/profile_pic/1259094587/original.jpg?aki_policy=profile_x_m...   
2  https://a0.muscache.com/im/users/8028/profile_pic/1329882962/original.jpg?aki_policy=profile_x_m...   
3  https://a0.muscache.com/im/users/8186/profile_pic/1272556663/original.jpg?aki_policy=profile_x_m...   
4  https://a0.muscache.com/im/pictures/4f35ef11-7f37-45cf-80da-f914a6d5f451.jpg?aki_policy=profile_...   

  host_neighbourhood  host_listings_count  host_total_listings_count  \
0      East Downtown                  3.0                        3.0   
1      East Downtown                  3.0                        3.0   
2      East Downtown                  1.0                        1.0   
3  SW Williamson Co.                  1.0                        1.0   
4     Travis Heights                  1.0                        1.0   

                                                                                    host_verifications  \
0                                                     ['email', 'phone', 'facebook', 'reviews', 'kba']   
1                                                     ['email', 'phone', 'facebook', 'reviews', 'kba']   
2                                                                 ['email', 'phone', 'reviews', 'kba']   
3                                ['email', 'phone', 'reviews', 'jumio', 'government_id', 'work_email']  

<b>From the next 20 columns, the following will remain</b>
	<ul>
    <li>neighbourhood_cleansed - zip code of the neighbourhood the listing is in</li>
    <li>neighbourhood - neighbourhood name the listing is in</li>
    </ul>

In [117]:
# Inspect the next 20 columns and first 5 rows
df.iloc[:5, 40:60]

neighbourhood_group_cleansed    city state zipcode  market smart_location  \
0                           NaN  Austin    TX   78702  Austin     Austin, TX   
1                           NaN  Austin    TX   78702  Austin     Austin, TX   
2                           NaN  Austin    TX   78702  Austin     Austin, TX   
3                           NaN  Austin    TX   78729  Austin     Austin, TX   
4                           NaN  Austin    TX   78704  Austin     Austin, TX   

  country_code        country  latitude  longitude is_location_exact  \
0           US  United States  30.27750  -97.71398                 f   
1           US  United States  30.27577  -97.71379                 t   
2           US  United States  30.26112  -97.73448                 t   
3           US  United States  30.45596  -97.78370                 t   
4           US  United States  30.24829  -97.73726                 t   

  property_type        room_type  accommodates  bathrooms  bedrooms  beds  \
0         House  Entire home/apt             4        2.0       2.0   2.0   
1         House     Private room             2        1.0       1.0   2.0   
2    Guesthouse  Entire home/apt             3        1.0       1.0   2.0   
3         House     Private room             2        1.0       1.0   1.0   
4    Guesthouse  Entire home/apt             2        1.0       NaN   1.0   

   bed_type  \
0  Real Bed   
1  Real Bed   
2  Real Bed   
3  Real Bed   
4  Real Bed   

                                                                                             amenities  \
0  {TV,"Cable TV",Internet,Wifi,"Air conditioning",Kitchen,"Free parking on premises","Paid parking...   
1  {TV,"Cable TV",Internet,Wifi,"Air conditioning",Kitchen,"Free parking on premises",Breakfast,"Pe...   
2  {TV,Wifi,"Air conditioning",Kitchen,"Pets live on this property",Dog(s),Cat(s),"Free street park...   
3  {TV,"Cable TV",Internet,Wifi,"Air conditioning",Kitchen,"Free parking on premises","Pets live on...   
4  {TV,"Cable TV",Internet,Wifi,"Air conditioning",Kitchen,"Pets live on this property",Cat(s),Heat...   

   square_feet  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4        550.0

<b>From the next 20 columns, the following will remain</b>
	<ul>
    <li>latitude - measurement location north or south of the equator</li>
    <li>longitude - measurement location east or west of the Prime Meridian </li>
    <li>room_type - type of listing space, ie. entire home or room</li>
    <li>accommodates - number of allowed guests</li>
    <li>bathrooms - number of bathrooms</li>
    <li>bedrooms - number of bedrooms</li>
    <li>beds - number of beds</li>
    </ul>

In [118]:
# Inspect the next 20 columns and first 5 rows
df.iloc[:5, 60:80]

price weekly_price monthly_price security_deposit cleaning_fee  \
0  $225.00          NaN           NaN          $500.00      $100.00   
1  $100.00          NaN           NaN          $500.00       $75.00   
2   $95.00          NaN           NaN          $100.00          NaN   
3   $40.00      $160.00           NaN              NaN          NaN   
4   $99.00      $700.00     $1,900.00              NaN       $50.00   

   guests_included extra_people  minimum_nights  maximum_nights  \
0                4       $30.00              30              90   
1                2       $35.00              30              60   
2                2       $45.00               2              90   
3                2        $0.00               1              14   
4                2       $25.00               3             365   

   minimum_minimum_nights  maximum_minimum_nights  minimum_maximum_nights  \
0                      30                      30                      90   
1                      30                      30                      60   
2                       2                       2                      90   
3                       1                       1                      14   
4                       3                       4                     365   

   maximum_maximum_nights  minimum_nights_avg_ntm  maximum_nights_avg_ntm  \
0                      90                    30.0                    90.0   
1                      60                    30.0                    60.0   
2                      90                     2.0                    90.0   
3                      14                     1.0                    14.0   
4                     365                     3.0                   365.0   

  calendar_updated has_availability  availability_30  availability_60  \
0      6 weeks ago                t                0                0   
1     3 months ago                t               11               11   
2      2 weeks ago                t                2               11   
3       3 days ago                t                6                6   
4       1 week ago                t                0                0   

   availability_90  
0                0  
1               11  
2               35  
3               13  
4                0

<b>From the next 20 columns, the following will remain</b>
	<ul>
    <li>price - average price per night</li>
    <li>minimum_nights - minimum amount of nights to book</li>
    </ul>

In [119]:
# Inspect the next 20 columns and first 5 rows
df.iloc[:5, 80:100]

availability_365 calendar_last_scraped  number_of_reviews  \
0                 0            2019-09-19                 24   
1                11            2019-09-19                  9   
2               291            2019-09-19                499   
3                13            2019-09-19                253   
4                 0            2019-09-19                100   

   number_of_reviews_ltm first_review last_review  review_scores_rating  \
0                      1   2009-03-17  2019-03-16                  93.0   
1                      0   2009-03-19  2018-03-14                  91.0   
2                     46   2009-03-08  2019-09-14                  96.0   
3                     16   2010-04-10  2019-08-22                  98.0   
4                     23   2009-12-14  2019-08-25                  99.0   

   review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  \
0                     9.0                       10.0                   10.0   
1                    10.0                        8.0                   10.0   
2                    10.0                       10.0                   10.0   
3                    10.0                       10.0                   10.0   
4                    10.0                       10.0                   10.0   

   review_scores_communication  review_scores_location  review_scores_value  \
0                         10.0                     8.0                  9.0   
1                          9.0                    10.0                  9.0   
2                         10.0                    10.0                 10.0   
3                         10.0                    10.0                 10.0   
4                         10.0                    10.0                 10.0   

  requires_license      license jurisdiction_names instant_bookable  \
0                f          NaN    {"Texas State"}                f   
1                f          NaN    {"Texas State"}                f   
2                f          NaN    {"Texas State"}                f   
3                f          NaN    {"Texas State"}                f   
4                f  32041657928    {"Texas State"}                t   

  is_business_travel_ready          cancellation_policy  \
0                        f  strict_14_with_grace_period   
1                        f  strict_14_with_grace_period   
2                        f  strict_14_with_grace_period   
3                        f                     moderate   
4                        f  strict_14_with_grace_period   

  require_guest_profile_picture  
0                             f  
1                             f  
2                             f  
3                             t  
4                             f

<b>From the next 20 columns, the following will remain</b>
	<ul>
    <li>number_of_reviews - number of reviews</li>
    <li>review_scores_rating - the rating score determined by reviews</li>
    </ul>

In [120]:
df.iloc[:5, 100:]

require_guest_phone_verification  calculated_host_listings_count  \
0                                f                               3   
1                                f                               3   
2                                t                               1   
3                                t                               1   
4                                f                               1   

   calculated_host_listings_count_entire_homes  \
0                                            2   
1                                            2   
2                                            1   
3                                            0   
4                                            1   

   calculated_host_listings_count_private_rooms  \
0                                             1   
1                                             1   
2                                             0   
3                                             1   
4                                             0   

   calculated_host_listings_count_shared_rooms  reviews_per_month  
0                                            0               0.19  
1                                            0               0.07  
2                                            0               3.89  
3                                            0               2.20  
4                                            0               0.84

<b>No columns will remain from the last set of columns.</b>

I will extract only the columns of interest, store them in a new dataframe and ensure all of the columns are there.

In [121]:
# Create new dataframe with important columns and inspect it
df = df[['id', 'neighbourhood_cleansed', 'neighbourhood', 'latitude', 'longitude', 
            'room_type', 'accommodates', 'bathrooms', 'bedrooms', 'beds',
            'price', 'minimum_nights', 'number_of_reviews', 
            'review_scores_rating']]

# Rename the id column to listing_id
df.rename(columns = {'id':'listing_id'}, inplace = True)

# Set index to the listing id
new_df = df.set_index('listing_id')

new_df.head(5)

neighbourhood_cleansed      neighbourhood  latitude  longitude  \
listing_id                                                                   
2265                         78702      East Downtown  30.27750  -97.71398   
5245                         78702      East Downtown  30.27577  -97.71379   
5456                         78702      East Downtown  30.26112  -97.73448   
5769                         78729  SW Williamson Co.  30.45596  -97.78370   
6413                         78704     Travis Heights  30.24829  -97.73726   

                  room_type  accommodates  bathrooms  bedrooms  beds    price  \
listing_id                                                                      
2265        Entire home/apt             4        2.0       2.0   2.0  $225.00   
5245           Private room             2        1.0       1.0   2.0  $100.00   
5456        Entire home/apt             3        1.0       1.0   2.0   $95.00   
5769           Private room             2        1.0       1.0   1.0   $40.00   
6413        Entire home/apt             2        1.0       NaN   1.0   $99.00   

            minimum_nights  number_of_reviews  review_scores_rating  
listing_id                                                           
2265                    30                 24                  93.0  
5245                    30                  9                  91.0  
5456                     2                499                  96.0  
5769                     1                253                  98.0  
6413                     3                100                  99.0

Between neighbourhood_cleansed and neighbourhood columns, it's more sensible to keep the one with name vesus zip code. There are multiple neighbourhood names for each zip code. For each zip code, I will determine which neighbourhood name it has most of and place them in a new column. Then I will drop the original neighbourhood_cleansed and neighbourhood columns.

In [122]:
# Get the count of each neighbourhood name grouped by zip codes
neighbourhood_df = new_df.groupby(['neighbourhood_cleansed', 'neighbourhood']).size().to_frame('count')

# Inspect the dataframe
neighbourhood_df.head(20)

count
neighbourhood_cleansed neighbourhood             
78701                  Downtown               625
                       Rainey Street           33
                       University of Texas      1
78702                  East Downtown         1071
                       Govalle                159
                       Holly                  135
                       Rosewood               119
                       Upper Boggy Creek        2
78703                  Bryker Woods            33
                       Clarksville            114
                       Downtown                39
                       Old Enfield             25
                       Old West Austin        197
                       Tarrytown              111
                       West Austin             76
78704                  Barton Hills           213
                       Bouldin Creek          352
                       Dawson                  97
                       Downtown                 1
                       East Riverside           2

For each zip code, I will keep the neighbourhood name it has the most of.

In [123]:
# For each zip code, get only the neighbourhood name that had the most counts
neighbourhood_df = neighbourhood_df.loc[neighbourhood_df.groupby(['neighbourhood_cleansed'])['count'].idxmax()]

# Reset the index
neighbourhood_df = neighbourhood_df.reset_index()

# Inspect the dataframe
neighbourhood_df.head(5)

neighbourhood_cleansed        neighbourhood  count
0                   78701             Downtown    625
1                   78702        East Downtown   1071
2                   78703      Old West Austin    197
3                   78704       Travis Heights    447
4                   78705  University of Texas    426

In [124]:
# Drop the count column
neighbourhood_df.drop(['count'], inplace=True, axis=1)

# Inspect the dropped column
neighbourhood_df.head()

neighbourhood_cleansed        neighbourhood
0                   78701             Downtown
1                   78702        East Downtown
2                   78703      Old West Austin
3                   78704       Travis Heights
4                   78705  University of Texas

In [125]:
# Drop the original neighbourhood column from the main dataframe
new_df.drop(['neighbourhood'], inplace=True, axis=1)

# Check that the column is removed
new_df.head()

neighbourhood_cleansed  latitude  longitude        room_type  \
listing_id                                                                 
2265                         78702  30.27750  -97.71398  Entire home/apt   
5245                         78702  30.27577  -97.71379     Private room   
5456                         78702  30.26112  -97.73448  Entire home/apt   
5769                         78729  30.45596  -97.78370     Private room   
6413                         78704  30.24829  -97.73726  Entire home/apt   

            accommodates  bathrooms  bedrooms  beds    price  minimum_nights  \
listing_id                                                                     
2265                   4        2.0       2.0   2.0  $225.00              30   
5245                   2        1.0       1.0   2.0  $100.00              30   
5456                   3        1.0       1.0   2.0   $95.00               2   
5769                   2        1.0       1.0   1.0   $40.00               1   
6413                   2        1.0       NaN   1.0   $99.00               3   

            number_of_reviews  review_scores_rating  
listing_id                                           
2265                       24                  93.0  
5245                        9                  91.0  
5456                      499                  96.0  
5769                      253                  98.0  
6413                      100                  99.0

In [126]:
# Reset the index
new_df = new_df.reset_index()

# Merge the neighbourbood data frame with the main dataframe and set the index back to listing_id
new_df = pd.merge(new_df, neighbourhood_df, on = ['neighbourhood_cleansed']).set_index('listing_id')

# Inspect the new dataframe
new_df.head()

neighbourhood_cleansed  latitude  longitude        room_type  \
listing_id                                                                 
2265                         78702  30.27750  -97.71398  Entire home/apt   
5245                         78702  30.27577  -97.71379     Private room   
5456                         78702  30.26112  -97.73448  Entire home/apt   
75174                        78702  30.24773  -97.72584  Entire home/apt   
76911                        78702  30.26775  -97.72695  Entire home/apt   

            accommodates  bathrooms  bedrooms  beds    price  minimum_nights  \
listing_id                                                                     
2265                   4        2.0       2.0   2.0  $225.00              30   
5245                   2        1.0       1.0   2.0  $100.00              30   
5456                   3        1.0       1.0   2.0   $95.00               2   
75174                  3        1.0       1.0   1.0  $130.00               2   
76911                 10        3.0       5.0  12.0  $821.00               2   

            number_of_reviews  review_scores_rating  neighbourhood  
listing_id                                                          
2265                       24                  93.0  East Downtown  
5245                        9                  91.0  East Downtown  
5456                      499                  96.0  East Downtown  
75174                     249                  98.0  East Downtown  
76911                     126                  99.0  East Downtown

I will test check some zip codes and ensure they are matched to the right neighbourhood name in the new neighhourhood column. 

In [127]:
# Ensure 78719 match to McKinney
test_78719 = new_df[new_df['neighbourhood_cleansed'] == 78719]

# Inspect the test
test_78719

neighbourhood_cleansed  latitude  longitude        room_type  \
listing_id                                                                 
16547602                     78719  30.17635  -97.68896     Private room   
21176644                     78719  30.09808  -97.66277  Entire home/apt   
22063431                     78719  30.15863  -97.69430  Entire home/apt   
26985305                     78719  30.17068  -97.69071  Entire home/apt   

            accommodates  bathrooms  bedrooms  beds    price  minimum_nights  \
listing_id                                                                     
16547602               2        1.5       1.0   2.0   $78.00              29   
21176644               6        1.0       2.0   7.0  $256.00               2   
22063431               6        2.0       3.0   3.0  $115.00               1   
26985305               6        2.0       3.0   3.0  $231.00               2   

            number_of_reviews  review_scores_rating neighbourhood  
listing_id                                                         
16547602                   25                  99.0      McKinney  
21176644                    5                 100.0      McKinney  
22063431                   68                  96.0      McKinney  
26985305                    2                  80.0      McKinney

The above test passed. 

In [128]:
# Ensure 78731 match to Northwest Hills
test_78731 = new_df[new_df['neighbourhood_cleansed'] == 78731]

# Inspect the test
test_78731

neighbourhood_cleansed  latitude  longitude        room_type  \
listing_id                                                                 
40285                        78731  30.35141  -97.76323  Entire home/apt   
72833                        78731  30.31383  -97.75161  Entire home/apt   
78993                        78731  30.32787  -97.75442  Entire home/apt   
430683                       78731  30.33945  -97.76182  Entire home/apt   
687675                       78731  30.35037  -97.75921  Entire home/apt   
...                            ...       ...        ...              ...   
37971719                     78731  30.35056  -97.75574  Entire home/apt   
38106797                     78731  30.34597  -97.78197     Private room   
38183019                     78731  30.30936  -97.75348  Entire home/apt   
38300333                     78731  30.32095  -97.75317     Private room   
38549249                     78731  30.32730  -97.75436  Entire home/apt   

            accommodates  bathrooms  bedrooms  beds    price  minimum_nights  \
listing_id                                                                     
40285                  4        2.0       2.0   2.0  $350.00               2   
72833                  2        1.0       1.0   2.0   $85.00               3   
78993                  5        2.5       3.0   4.0  $500.00               2   
430683                 5        2.0       3.0   3.0  $625.00               2   
687675                 8        2.0       3.0   4.0  $275.00               2   
...                  ...        ...       ...   ...      ...             ...   
37971719               8        2.0       3.0   5.0  $199.00               1   
38106797               4        1.0       1.0   1.0   $75.00               1   
38183019               3        1.0       1.0   1.0   $89.00               1   
38300333               2        1.0       1.0   1.0   $85.00               2   
38549249               6        1.0       3.0   3.0  $280.00               2   

            number_of_reviews  review_scores_rating    neighbourhood  
listing_id                                                            
40285                      30                  98.0  Northwest Hills  
72833                     320                  98.0  Northwest Hills  
78993                      10                 100.0  Northwest Hills  
430683                     10                 100.0  Northwest Hills  
687675                     65                  94.0  Northwest Hills  
...                       ...                   ...              ...  
37971719                    0                   NaN  Northwest Hills  
38106797                    1                 100.0  Northwest Hills  
38183019                    2                 100.0  Northwest Hills  
38300333                    0                   NaN  Northwest Hills  
38549249                    0                   NaN  Northwest Hills  

[150 rows x 13 columns]

The above test passed.

In [129]:
# Ensure 78723 match to Mueller
test_78723 = new_df[new_df['neighbourhood_cleansed'] == 78723]

# Inspect the test
test_78723

neighbourhood_cleansed  latitude  longitude        room_type  \
listing_id                                                                 
79100                        78723  30.30971  -97.69480  Entire home/apt   
82033                        78723  30.30419  -97.68914  Entire home/apt   
247770                       78723  30.30340  -97.68496  Entire home/apt   
356719                       78723  30.30599  -97.69641  Entire home/apt   
607536                       78723  30.30267  -97.67915     Private room   
...                            ...       ...        ...              ...   
38099791                     78723  30.29829  -97.68355  Entire home/apt   
38101314                     78723  30.30485  -97.67276  Entire home/apt   
38328886                     78723  30.30736  -97.68243  Entire home/apt   
38670989                     78723  30.31499  -97.67790  Entire home/apt   
38674492                     78723  30.29676  -97.68565  Entire home/apt   

            accommodates  bathrooms  bedrooms  beds    price  minimum_nights  \
listing_id                                                                     
79100                  2        1.0       1.0   1.0  $125.00              30   
82033                 12        2.0       3.0   5.0  $508.00               1   
247770                 5        NaN       3.0   2.0  $175.00               2   
356719                 9        2.0       3.0   3.0  $325.00               2   
607536                 4        1.5       2.0   2.0   $70.00               1   
...                  ...        ...       ...   ...      ...             ...   
38099791               6        2.0       3.0   3.0  $900.00               1   
38101314               7        1.0       2.0   5.0   $74.00               1   
38328886              10        2.0       5.0   6.0  $250.00               1   
38670989               5        3.0       2.0   2.0  $250.00               2   
38674492               4        1.0       1.0   1.0   $63.00               1   

            number_of_reviews  review_scores_rating neighbourhood  
listing_id                                                         
79100                      29                  97.0       Mueller  
82033                       4                  65.0       Mueller  
247770                      1                  80.0       Mueller  
356719                      1                 100.0       Mueller  
607536                    100                  97.0       Mueller  
...                       ...                   ...           ...  
38099791                    0                   NaN       Mueller  
38101314                    0                   NaN       Mueller  
38328886                    3                 100.0       Mueller  
38670989                    0                   NaN       Mueller  
38674492                    0                   NaN       Mueller  

[344 rows x 13 columns]

The above test passed.

Change the neighbourhood_cleansed column to zip_code. I will keep this column for geo mapping in the exploratory data analysis process.

In [130]:
# Drop the original neighbourhood_cleansed column from the main dataframe
new_df.rename(columns = {'neighbourhood_cleansed':'zip_code'}, inplace = True)

# Check that the column is removed
new_df.head()

zip_code  latitude  longitude        room_type  accommodates  \
listing_id                                                                 
2265           78702  30.27750  -97.71398  Entire home/apt             4   
5245           78702  30.27577  -97.71379     Private room             2   
5456           78702  30.26112  -97.73448  Entire home/apt             3   
75174          78702  30.24773  -97.72584  Entire home/apt             3   
76911          78702  30.26775  -97.72695  Entire home/apt            10   

            bathrooms  bedrooms  beds    price  minimum_nights  \
listing_id                                                       
2265              2.0       2.0   2.0  $225.00              30   
5245              1.0       1.0   2.0  $100.00              30   
5456              1.0       1.0   2.0   $95.00               2   
75174             1.0       1.0   1.0  $130.00               2   
76911             3.0       5.0  12.0  $821.00               2   

            number_of_reviews  review_scores_rating  neighbourhood  
listing_id                                                          
2265                       24                  93.0  East Downtown  
5245                        9                  91.0  East Downtown  
5456                      499                  96.0  East Downtown  
75174                     249                  98.0  East Downtown  
76911                     126                  99.0  East Downtown

For my exploratory analysis later, I will need some information related to amount of calendar bookings per listing from the past year. I will put these values into a new column. Then I will merge the dataframe with the main dataframe.

In [131]:
# Read in detailed calendar data 
df_calendar = pd.read_csv('Data/calendar.csv')

# Get subset of calendar data where the listing was not available, ie., booked
df_calendar  = df_calendar[df_calendar['available'] == 'f']

# Get amount of bookings this year per listing 
df_calendar = df_calendar.groupby('listing_id').size().to_frame()

# Change column name to something more sensible
df_calendar.columns = ['number_of_bookings']

# Inspect the calendar dataframe
df_calendar.head()

number_of_bookings
listing_id                    
2265                       365
5245                       354
5456                        74
5769                       352
6413                       365

In [132]:
# Merge the calendar data with the main dataframe
new_df = pd.merge(left=new_df, right=df_calendar, how='left', left_on='listing_id', right_on='listing_id')

# Check if there are any missing values
new_df['number_of_bookings'].isnull().value_counts()

False    11016
True       323
Name: number_of_bookings, dtype: int64

There are 323 missing number_of_bookings values. This is likely because these particular listings do not have any bookings yet. I will set the number_of_bookings of them to zero

In [133]:
# For the missing values in number_of_bookings column due to no bookings yet, set to zero
new_df['number_of_bookings'] = new_df['number_of_bookings'].fillna(0)

# Check if there are any more missing values
new_df['number_of_bookings'].isnull().value_counts()

False    11339
Name: number_of_bookings, dtype: int64

There are no more missing values in the number_of_bookings column. 

In [134]:
# Inspect the updated dataframe
new_df.info()
new_df.tail()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11339 entries, 2265 to 33812177
Data columns (total 14 columns):
zip_code                11339 non-null int64
latitude                11339 non-null float64
longitude               11339 non-null float64
room_type               11339 non-null object
accommodates            11339 non-null int64
bathrooms               11321 non-null float64
bedrooms                11332 non-null float64
beds                    11328 non-null float64
price                   11339 non-null object
minimum_nights          11339 non-null int64
number_of_reviews       11339 non-null int64
review_scores_rating    8759 non-null float64
neighbourhood           11339 non-null object
number_of_bookings      11339 non-null float64
dtypes: float64(7), int64(4), object(3)
memory usage: 1.3+ MB


zip_code  latitude  longitude        room_type  accommodates  \
listing_id                                                                 
17531239       78742  30.24210  -97.68920  Entire home/apt             2   
29036642       78742  30.22863  -97.65910  Entire home/apt             2   
29362841       78742  30.22870  -97.65978  Entire home/apt             2   
33741923       78742  30.22927  -97.66380  Entire home/apt             2   
33812177       78742  30.23072  -97.66146  Entire home/apt             2   

            bathrooms  bedrooms  beds    price  minimum_nights  \
listing_id                                                       
17531239          1.0       1.0   1.0  $125.00               2   
29036642          1.0       1.0   1.0  $100.00               1   
29362841          1.0       1.0   1.0  $100.00               1   
33741923          1.0       1.0   1.0  $100.00               1   
33812177          1.0       1.0   1.0  $100.00               1   

            number_of_reviews  review_scores_rating neighbourhood  \
listing_id                                                          
17531239                   37                  98.0    Montopolis   
29036642                    7                  97.0    Montopolis   
29362841                    6                 100.0    Montopolis   
33741923                    2                 100.0    Montopolis   
33812177                    1                  80.0    Montopolis   

            number_of_bookings  
listing_id                      
17531239                 365.0  
29036642                 320.0  
29362841                 365.0  
33741923                 243.0  
33812177                 274.0

Now I will drop any duplicates.

In [135]:
# Drop any duplicates in the data
new_df.drop_duplicates()
new_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11339 entries, 2265 to 33812177
Data columns (total 14 columns):
zip_code                11339 non-null int64
latitude                11339 non-null float64
longitude               11339 non-null float64
room_type               11339 non-null object
accommodates            11339 non-null int64
bathrooms               11321 non-null float64
bedrooms                11332 non-null float64
beds                    11328 non-null float64
price                   11339 non-null object
minimum_nights          11339 non-null int64
number_of_reviews       11339 non-null int64
review_scores_rating    8759 non-null float64
neighbourhood           11339 non-null object
number_of_bookings      11339 non-null float64
dtypes: float64(7), int64(4), object(3)
memory usage: 1.3+ MB


The numbers haven't changed so there were no duplicates rows.

In general, the cleaning and preparation also involves fixing structural issues, handling missing data and managing outliers. These processes will be explained in more detail.

# CLEANING THE DATA
First I will inspect the new dataframe on it's data types.

In [136]:
# Check for data types and missing values
new_df.info(verbose = True, null_counts=True)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11339 entries, 2265 to 33812177
Data columns (total 14 columns):
zip_code                11339 non-null int64
latitude                11339 non-null float64
longitude               11339 non-null float64
room_type               11339 non-null object
accommodates            11339 non-null int64
bathrooms               11321 non-null float64
bedrooms                11332 non-null float64
beds                    11328 non-null float64
price                   11339 non-null object
minimum_nights          11339 non-null int64
number_of_reviews       11339 non-null int64
review_scores_rating    8759 non-null float64
neighbourhood           11339 non-null object
number_of_bookings      11339 non-null float64
dtypes: float64(7), int64(4), object(3)
memory usage: 1.3+ MB


<b>Upon observation, I will do the following</b>
<ul>
    <li>update price object type to float type</li>
    <li>update neighbourhood object type to category type</li>
     <li>update room_type object type to categorical type</li>
    <li>handle missing values in bathrooms, bedrooms, beds and review_scores_rating </li>
</ul>

The price column contains the $ symbol so it may be a string. I will check to see if it is of string data type. If so, I will need to convert the column to a float. This will make help with aggregations and visualizations later in the process.

In [137]:
# Check if the 'price' Series is of string type
is_string_dtype(new_df['price'])

True

In [138]:
# Remove all $ and , symbols from the 'price' Series and convert the values from string to float type
new_df.loc[:,'price'] = new_df.loc[:,'price'].str.replace('[,$]', '', regex=True).astype(float)

# Check the updated data type
new_df['price'].dtype

dtype('float64')

I will convert property_type and room_type object to either categorical.



In [139]:
# Select columns to be of categorical type
new_df['room_type'] = new_df['room_type'].astype('category')
new_df['room_type'].dtypes

CategoricalDtype(categories=['Entire home/apt', 'Hotel room', 'Private room',
                  'Shared room'],
                 ordered=False)

In [140]:
# Select columns to be of categorical type
new_df['neighbourhood'] = new_df['neighbourhood'].astype('category')
new_df['neighbourhood'].dtypes

CategoricalDtype(categories=['Anderson Mill', 'Balcones Civic Association',
                  'Barton Creek', 'Brentwood', 'Cherry Creek', 'Circle C',
                  'Copperfield', 'Crestview', 'Downtown', 'East Downtown',
                  'East Riverside', 'Gracywoods', 'Highland',
                  'Lamplight Village', 'Long Canyon', 'MLK & 183', 'McKinney',
                  'Montopolis', 'Mueller', 'North Loop', 'Northwest Hills',
                  'Oak Hill', 'Old West Austin', 'SW Williamson Co.',
                  'Scofield Ridge', 'South Manchaca', 'Steiner Ranch',
                  'Travis Heights', 'University Hills', 'University of Texas',
                  'Upper Boggy Creek', 'Westlake Hills'],
                 ordered=False)

Since the review_scores_rating column has more than 20% missing values, I will inspect the data related to reviews further to determine how I should handle it. More specifically, I will take a look at the rows which have a missing review_scores_rating value.

In [141]:
# Get subset of dataframe that is related to reviews 
reviews = new_df[['number_of_reviews', 'review_scores_rating']]

# Get subset of reviews that has a missing review score
reviews_nan = reviews[pd.isnull(reviews['review_scores_rating'])]
reviews_nan.head(10)

number_of_reviews  review_scores_rating
listing_id                                         
342919                      0                   NaN
370115                      0                   NaN
788073                      0                   NaN
947423                      0                   NaN
966550                      0                   NaN
1640348                     0                   NaN
2183323                     0                   NaN
2303288                     0                   NaN
2325410                     0                   NaN
2368211                     0                   NaN

As suspected, there are several rows with 0 number_of_reviews, therefore the review_scores_rating cannot be calculated. I will flag these with a -1. 

In [142]:
# Loop through the data frame, update review_scores_rating to -1 if the number_of_reviews is 0 
for i, row in new_df.iterrows():
    if row['number_of_reviews'] == 0:
       new_df.loc[i, 'review_scores_rating'] = -1

# Check that the column is updated to -1 for the appropiate rows
check_df = new_df[new_df['review_scores_rating'] == -1]
check_df.head(5)

zip_code  latitude  longitude        room_type  accommodates  \
listing_id                                                                 
342919         78702  30.25820  -97.72019  Entire home/apt             3   
370115         78702  30.27368  -97.71552  Entire home/apt             5   
788073         78702  30.26001  -97.69581  Entire home/apt             5   
947423         78702  30.25977  -97.69713     Private room             8   
966550         78702  30.27310  -97.71986  Entire home/apt             4   

            bathrooms  bedrooms  beds  price  minimum_nights  \
listing_id                                                     
342919            NaN       2.0   1.0  400.0               3   
370115            2.5       2.0   2.0  750.0               2   
788073            1.0       2.0   2.0  200.0               3   
947423            2.0       1.0   1.0  250.0               3   
966550            1.0       1.0   3.0  295.0               3   

            number_of_reviews  review_scores_rating  neighbourhood  \
listing_id                                                           
342919                      0                  -1.0  East Downtown   
370115                      0                  -1.0  East Downtown   
788073                      0                  -1.0  East Downtown   
947423                      0                  -1.0  East Downtown   
966550                      0                  -1.0  East Downtown   

            number_of_bookings  
listing_id                      
342919                   365.0  
370115                   365.0  
788073                     1.0  
947423                     0.0  
966550                     0.0

Interestingly, there are some rows with more than 0 number_of_reviews still resulting in missing values. I will inspect this further by looking at the rows with numbers_of_reviews > 0 and reviews_score_rating = 0.

In [143]:
# Get subset of previous reviews subset that have more than 0 number of reviews
reviews_nan_notzero = reviews_nan[reviews_nan['number_of_reviews'] > 0]

# Get the count of how many records have more than 0 number of reviews and missing review scores
print(reviews_nan_notzero.count())
reviews_nan_notzero.head(5)

number_of_reviews       120
review_scores_rating      0
dtype: int64


number_of_reviews  review_scores_rating
listing_id                                         
16987710                    1                   NaN
19165667                    2                   NaN
22076766                    1                   NaN
23394163                    1                   NaN
28486334                    1                   NaN

I will pull in the detailed reviews data for further analysis and inspect the first 5 records.

In [144]:
# Pull in the detailed reviews data into a data frame
df_reviews = pd.read_csv('Data/reviews.csv')
df_reviews.head(5)

listing_id       id        date  reviewer_id reviewer_name  \
0        2265      963  2009-03-17         7538         Niall   
1        2265     1057  2009-03-22        10029       Michael   
2        2265   200418  2011-03-16        61677        Gustaf   
3        2265  1001630  2012-03-15      1523753          Noah   
4        2265  1016390  2012-03-19      1547660       Melissa   

                                                                                              comments  
0  I stayed here during SXSW and had a really pleasant stay.  The house is a very relaxing environm...  
1  Great place, close enough to everything downtown Austin has, yet just far enough to be relaxing ...  
2  We had a great time in Austin staying at Paddy's house. The house is much larger than it looks o...  
3  We had a great stay at Zen East for South By Southwest!  Paddy was extremely accommodating and w...  
4  I arrived late in the evening so did not meet Paddy, but her home was lovely and clean and welco...

In [145]:
# Set index as the listing id and get a subset of the important columns
df_reviews = df_reviews.set_index('listing_id')
df_reviews = df_reviews[['date', 'comments']]
df_reviews.head(5)

date  \
listing_id               
2265        2009-03-17   
2265        2009-03-22   
2265        2011-03-16   
2265        2012-03-15   
2265        2012-03-19   

                                                                                                       comments  
listing_id                                                                                                       
2265        I stayed here during SXSW and had a really pleasant stay.  The house is a very relaxing environm...  
2265        Great place, close enough to everything downtown Austin has, yet just far enough to be relaxing ...  
2265        We had a great time in Austin staying at Paddy's house. The house is much larger than it looks o...  
2265        We had a great stay at Zen East for South By Southwest!  Paddy was extremely accommodating and w...  
2265        I arrived late in the evening so did not meet Paddy, but her home was lovely and clean and welco...

<b>I will combine the following two dataframes for further inspection</b>
<ul>
    <li>df_reviews - subset of detailed reviews data containing the date and comments for each listing_id</li>
    <li>reviews_nan_notzero - subset of detailed listings data containing listing id where number of reviews > 0
    and review scores are missing</li>
</ul>

In [146]:
# Combine the 2 relevant dataframes
nan_df_review = pd.merge(df_reviews, reviews_nan_notzero, on='listing_id')

# Expand the cell to allow more characters
pd.set_option('max_colwidth', 100)

# Subset the records that have more than 0 number of reviews
nan_df_review = nan_df_review[nan_df_review['number_of_reviews'] > 0]
nan_df_review

date  \
listing_id               
318963      2012-01-26   
321069      2018-06-23   
942843      2013-07-31   
2385724     2016-09-26   
2385724     2016-11-20   
...                ...   
38297689    2019-09-08   
38596517    2019-09-13   
38646013    2019-09-17   
38703706    2019-09-18   
38727516    2019-09-18   

                                                                                             comments  \
listing_id                                                                                              
318963                                       The host canceled my reservation 45 days before arrival.   
321069      The host canceled this reservation 104 days before arrival. This is an automated posting.   
942843              The reservation was canceled 7 days before arrival. This is an automated posting.   
2385724      The host canceled this reservation 32 days before arrival. This is an automated posting.   
2385724      The host canceled this reservation 33 days before arrival. This is an automated posting.   
...                                                                                               ...   
38297689     The host canceled this reservation 20 days before arrival. This is an automated posting.   
38596517     The host canceled this reservation 21 days before arrival. This is an automated posting.   
38646013     The host canceled this reservation 44 days before arrival. This is an automated posting.   
38703706     The host canceled this reservation 15 days before arrival. This is an automated posting.   
38727516     The host canceled this reservation 22 days before arrival. This is an automated posting.   

            number_of_reviews  review_scores_rating  
listing_id                                           
318963                      1                   NaN  
321069                      1                   NaN  
942843                      1                   NaN  
2385724                     2                   NaN  
2385724                     2                   NaN  
...                       ...                   ...  
38297689                    1                   NaN  
38596517                    1                   NaN  
38646013                    1                   NaN  
38703706                    1                   NaN  
38727516                    1                   NaN  

[141 rows x 4 columns]

141 rows returned. If the listing has more than 0 number_of_reviews and has a missing review_scores_rating, there is a commonality of an automated review comment due to a cancelled reservation. 

There is for sure at least one comment that says it was canceled but there was no automated text. I suspect that there was an update to the system after this post was created. I will loop through the nan_df_review dataframe and check each record for either the automated text comment or host cancellation comment. If there's a match, I will keep track of the listing id in a new dataframe.

In [147]:
# Create an empty dataframe with column listing_id
listings_df = pd.DataFrame(columns=['listing_id'])

# Reset the index 
nan_df_review = nan_df_review.reset_index()

# Loop through the nan_df_review dataframe and find which records have the automated posting text or 
# host cancellation text. If the record comment matches, add the listing_id of that review to the 
# listings_df dataframe
for i, review in nan_df_review.iterrows():
    if bool(re.findall(r"\bautomated posting\b|\bhost canceled\b", review['comments'])) == True:
        listings_df.loc[i] = review['listing_id']

# Inspect the listings_df dataframe
listings_df.head(10)

listing_id
0     318963
1     321069
2     942843
3    2385724
4    2385724
5    4356661
6    5593402
7    5631123
8    7492335
9    8383427

I will drop any duplicates in the listings_df dataframe.

In [148]:
listings_df.drop_duplicates()

listing_id
0       318963
1       321069
2       942843
3      2385724
5      4356661
..         ...
136   38297689
137   38596517
138   38646013
139   38703706
140   38727516

[120 rows x 1 columns]

After dropping duplicates, 120 listings remain. 

Now I will loop through the main dataframe and match the listings from listings_df. For each matching record, I will flag the review_scores_rating value with -1.

In [149]:
# Reset the index
new_df = new_df.reset_index()

# Loop through the main dataframe to impute the review_scores_rating to -1 if the 
# listing_id matches 
for i, row_df_review in new_df.iterrows():
    for x, row_listing_id in listings_df.iterrows():
        if row_df_review['listing_id'] == row_listing_id['listing_id']:
            new_df.loc[i, 'review_scores_rating'] = -1

# Check if the -1 values were imputed           
check_df = new_df[new_df['number_of_reviews'] > 0]
check_df = check_df[check_df['review_scores_rating'] == -1]
check_df.head()

listing_id  zip_code  latitude  longitude        room_type  \
527     16987710     78702  30.25204  -97.72499  Entire home/apt   
628     19165667     78702  30.25108  -97.70235  Entire home/apt   
746     22076766     78702  30.25731  -97.72121  Entire home/apt   
815     23394163     78702  30.26462  -97.73352  Entire home/apt   
1047    28486334     78702  30.26010  -97.69528  Entire home/apt   

      accommodates  bathrooms  bedrooms  beds  price  minimum_nights  \
527              8        1.0       3.0   4.0  500.0               3   
628              2        1.0       2.0   2.0  175.0               3   
746              5        1.0       2.0   2.0  140.0               2   
815              2        1.0       1.0   1.0  400.0               1   
1047             6        2.0       3.0   2.0  112.0               3   

      number_of_reviews  review_scores_rating  neighbourhood  \
527                   1                  -1.0  East Downtown   
628                   2                  -1.0  East Downtown   
746                   1                  -1.0  East Downtown   
815                   1                  -1.0  East Downtown   
1047                  1                  -1.0  East Downtown   

      number_of_bookings  
527                275.0  
628                365.0  
746                365.0  
815                365.0  
1047               365.0

In [150]:
new_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11339 entries, 0 to 11338
Data columns (total 15 columns):
listing_id              11339 non-null int64
zip_code                11339 non-null int64
latitude                11339 non-null float64
longitude               11339 non-null float64
room_type               11339 non-null category
accommodates            11339 non-null int64
bathrooms               11321 non-null float64
bedrooms                11332 non-null float64
beds                    11328 non-null float64
price                   11339 non-null float64
minimum_nights          11339 non-null int64
number_of_reviews       11339 non-null int64
review_scores_rating    11339 non-null float64
neighbourhood           11339 non-null category
number_of_bookings      11339 non-null float64
dtypes: category(2), float64(8), int64(5)
memory usage: 1.1 MB


There are no more missing values in the review_scores_rating column. Now I will proceed on handling the missing bathrooms, bedrooms and beds values.

For missing bathrooms, bedrooms and beds I will create a function that will impute the median of the feature based on a correlated feature. For example, in the case of missing bathrooms value, if the record has a one bedroom, I will impute the median number of bathrooms for all one bedroom listings. 

In [151]:
# Define function for imputing the mean based on the missing feature value and correlated feature
def impute_median(df, impute_median, corr):
    for i, record in df.iterrows():
        median = int(new_df[new_df[corr] == record[corr]][impute_median].median())
        new_df.loc[i, impute_median] = median

Check the distribution before imputing the median for bathrooms. I will ensure the imputation does not drastically impact the distribution. If it doesn't, impute the median value. 

In [152]:
new_df['bathrooms'].describe()

count    11321.000000
mean         1.550062
std          0.891723
min          0.000000
25%          1.000000
50%          1.000000
75%          2.000000
max         17.000000
Name: bathrooms, dtype: float64

Impute the median number of bathrooms based on correlated number of bedrooms using the impute_median function.

In [153]:
# Get subset of dataaframe where there is missing bathrooms data
nan_bathroom = new_df[pd.isnull(new_df['bathrooms'])]

# Call function to impute the mean
impute_median(df=nan_bathroom, impute_median='bathrooms', corr='bedrooms')

Check the distribution of bathrooms.

In [154]:
new_df['bathrooms'].describe()

count    11339.000000
mean         1.550071
std          0.892224
min          0.000000
25%          1.000000
50%          1.000000
75%          2.000000
max         17.000000
Name: bathrooms, dtype: float64

The distribution hasn't changed. Check the distribution before imputing the median for bedrooms. I will ensure the imputation does not drastically impact the distribution. If it doesn't, impute the median value.

In [155]:
new_df['bedrooms'].describe()

count    11332.000000
mean         1.787857
std          1.268618
min          0.000000
25%          1.000000
50%          1.000000
75%          2.000000
max         23.000000
Name: bedrooms, dtype: float64

Impute the median number of bedrooms based on correlated number of bathrooms using the impute_median function.

In [156]:
# Get subset of dataaframe where there is missing bedrooms data
nan_bedrooms = new_df[pd.isnull(new_df['bedrooms'])]

# Call function to impute the mean
impute_median(df=nan_bedrooms, impute_median='bedrooms', corr='bathrooms')  

Check the distribution of bedrooms.

In [157]:
new_df['bedrooms'].describe()

count    11339.000000
mean         1.787371
std          1.268377
min          0.000000
25%          1.000000
50%          1.000000
75%          2.000000
max         23.000000
Name: bedrooms, dtype: float64

The distribution hasn't changed much. Check the distribution before imputing the median for beds. I will ensure the imputation does not drastically impact the distribution. If it doesn't, impute the median value.

In [158]:
new_df['beds'].describe()

count    11328.000000
mean         2.556321
std          2.787872
min          0.000000
25%          1.000000
50%          2.000000
75%          3.000000
max        132.000000
Name: beds, dtype: float64

Impute the median number of bed based on correlated number of accommodates using the impute_median function.

In [159]:
# Get subset of dataaframe where there is missing beds data
nan_beds = new_df[pd.isnull(new_df['beds'])]

# Call function to impute the mean
impute_median(df=nan_beds, impute_median='beds', corr='accommodates')   

Check the distribution of bedrooms.

In [160]:
new_df['beds'].describe()

count    11339.000000
mean         2.556663
std          2.787885
min          0.000000
25%          1.000000
50%          2.000000
75%          3.000000
max        132.000000
Name: beds, dtype: float64

The distribution hasn't changed much.

Inspect that all data types are correct and there is no more missing data.

In [161]:
new_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11339 entries, 0 to 11338
Data columns (total 15 columns):
listing_id              11339 non-null int64
zip_code                11339 non-null int64
latitude                11339 non-null float64
longitude               11339 non-null float64
room_type               11339 non-null category
accommodates            11339 non-null int64
bathrooms               11339 non-null float64
bedrooms                11339 non-null float64
beds                    11339 non-null float64
price                   11339 non-null float64
minimum_nights          11339 non-null int64
number_of_reviews       11339 non-null int64
review_scores_rating    11339 non-null float64
neighbourhood           11339 non-null category
number_of_bookings      11339 non-null float64
dtypes: category(2), float64(8), int64(5)
memory usage: 1.1 MB


Now that all bathrooms to bedrooms have no missing values, I will use these two columns to calculate the bathroom to bedroom ratio for each listing. This feature will help with exploratory data analysis later. For the listings that have 0 bathrooms and 0 bedrooms, I will set the bedroom_bath_ratio value to 0. For the listings that have 1 or more bathrooms and 0 bedrooms, I will flag the bedroom_bath_ratio value to -1.

In [162]:
# Calculate the bathroom to bedroom ratio
new_df['bedroom_bath_ratio'] = (new_df['bathrooms'] / new_df['bedrooms']) * 100

# For records that have 0 bathrooms and 0 bedrooms, set bedroom_bath_ratio to 0. If bathrooms is more than 0 
# and bedrooms is 0, flag these values with -1.
for i, record in new_df.iterrows():
    if record['bathrooms'] == 0.0 and record['bedrooms'] == 0.0:
        new_df.loc[i, 'bedroom_bath_ratio'] = 0.0
    if record['bathrooms'] > 0 and record['bedrooms'] == 0.0:
        new_df.loc[i, 'bedroom_bath_ratio'] = -1

# Inspect the dataframe
new_df.head(20)

listing_id  zip_code  latitude  longitude        room_type  accommodates  \
0         2265     78702  30.27750  -97.71398  Entire home/apt             4   
1         5245     78702  30.27577  -97.71379     Private room             2   
2         5456     78702  30.26112  -97.73448  Entire home/apt             3   
3        75174     78702  30.24773  -97.72584  Entire home/apt             3   
4        76911     78702  30.26775  -97.72695  Entire home/apt            10   
5        78422     78702  30.27324  -97.71173     Private room             2   
6        78584     78702  30.26278  -97.73529  Entire home/apt             6   
7        78731     78702  30.26984  -97.72874     Private room             2   
8        79768     78702  30.26071  -97.73258  Entire home/apt             4   
9       141550     78702  30.25582  -97.72709  Entire home/apt             3   
10      208897     78702  30.26350  -97.70097  Entire home/apt             9   
11      237705     78702  30.25409  -97.72566  Entire home/apt             8   
12      240541     78702  30.25426  -97.72431  Entire home/apt             2   
13      244785     78702  30.27917  -97.71564  Entire home/apt             4   
14      248515     78702  30.25434  -97.72825  Entire home/apt             4   
15      281182     78702  30.28091  -97.70809  Entire home/apt            10   
16      305392     78702  30.25518  -97.73289  Entire home/apt            10   
17      317148     78702  30.26764  -97.70976  Entire home/apt             6   
18      319759     78702  30.26480  -97.73428  Entire home/apt            16   
19      319887     78702  30.25536  -97.72855  Entire home/apt             5   

    bathrooms  bedrooms  beds  price  minimum_nights  number_of_reviews  \
0         2.0       2.0   2.0  225.0              30                 24   
1         1.0       1.0   2.0  100.0              30                  9   
2         1.0       1.0   2.0   95.0               2                499   
3         1.0       1.0   1.0  130.0               2                249   
4         3.0       5.0  12.0  821.0               2                126   
5         1.0       1.0   2.0   50.0               1                  1   
6         2.0       2.0   2.0  176.0               2                111   
7         1.0       1.0   1.0   85.0               2                166   
8         1.0       2.0   3.0  225.0               4                 34   
9         1.0       0.0   1.0  111.0               1                414   
10        1.0       3.0   3.0  184.0               2                 71   
11        2.0       3.0   4.0  450.0               1                 39   
12        1.0       1.0   1.0   81.0               1                330   
13        1.0       1.0   2.0   90.0               1                579   
14        1.0       2.0   2.0  375.0               2                 21   
15        2.5       3.0   3.0  350.0               3                 33   
16        3.0       4.0   5.0  525.0               4                  9   
17        1.0       2.0   2.0  250.0               2                 37   
18        3.5       3.0  10.0  200.0               2                205   
19        1.0       2.0   3.0  650.0               4                  2   

    review_scores_rating  neighbourhood  number_of_bookings  \
0                   93.0  East Downtown               365.0   
1                   91.0  East Downtown               354.0   
2                   96.0  East Downtown                74.0   
3                   98.0  East Downtown               131.0   
4                   99.0  East Downtown                56.0   
5                   60.0  East Downtown               320.0   
6                   99.0  East Downtown               253.0   
7                  100.0  East Downtown               290.0   
8                   94.0  East Downtown               365.0   
9                   97.0  East Downtown               244.0   
10                  99.0  East Downtown               

In [163]:
# Check if there are any missing values in bedroom_bath_ratio
new_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11339 entries, 0 to 11338
Data columns (total 16 columns):
listing_id              11339 non-null int64
zip_code                11339 non-null int64
latitude                11339 non-null float64
longitude               11339 non-null float64
room_type               11339 non-null category
accommodates            11339 non-null int64
bathrooms               11339 non-null float64
bedrooms                11339 non-null float64
beds                    11339 non-null float64
price                   11339 non-null float64
minimum_nights          11339 non-null int64
number_of_reviews       11339 non-null int64
review_scores_rating    11339 non-null float64
neighbourhood           11339 non-null category
number_of_bookings      11339 non-null float64
bedroom_bath_ratio      11339 non-null float64
dtypes: category(2), float64(9), int64(5)
memory usage: 1.2 MB


There are no more missing values so I will proceed to handling any outliers.

# HANDLING OUTLIERS

In [164]:
# View the basic statistical details of specific columns of the dataframe
new_df[['accommodates', 'bathrooms', 'bedrooms', 'beds', 'price', 'minimum_nights', 'number_of_reviews',
        'review_scores_rating', 'number_of_bookings']].describe(percentiles=[.01, .1, .25, .5, .75, .9, .99])

accommodates     bathrooms      bedrooms          beds        price  \
count  11339.000000  11339.000000  11339.000000  11339.000000  11339.00000   
mean       4.710821      1.550071      1.787371      2.556663    390.70112   
std        3.258878      0.892224      1.268377      2.787885   1128.82863   
min        1.000000      0.000000      0.000000      0.000000      0.00000   
1%         1.000000      1.000000      0.000000      1.000000     23.00000   
10%        2.000000      1.000000      1.000000      1.000000     50.00000   
25%        2.000000      1.000000      1.000000      1.000000     80.00000   
50%        4.000000      1.000000      1.000000      2.000000    145.00000   
75%        6.000000      2.000000      2.000000      3.000000    300.00000   
90%        8.200000      2.500000      3.000000      5.000000    669.00000   
99%       16.000000      5.000000      6.000000     12.000000  10000.00000   
max       32.000000     17.000000     23.000000    132.000000  17999.00000   

       minimum_nights  number_of_reviews  review_scores_rating  \
count    11339.000000       11339.000000          11339.000000   
mean         5.082988          29.006262             74.100626   
std         20.223087          58.114834             41.192930   
min          1.000000           0.000000             -1.000000   
1%           1.000000           0.000000             -1.000000   
10%          1.000000           0.000000             -1.000000   
25%          1.000000           1.000000             80.000000   
50%          2.000000           6.000000             97.000000   
75%          2.000000          29.000000            100.000000   
90%          5.000000          85.000000            100.000000   
99%         31.000000         279.100000            100.000000   
max        999.000000         856.000000            100.000000   

       number_of_bookings  
count        11339.000000  
mean           233.398360  
std            135.097541  
min              0.000000  
1%               0.000000  
10%             21.000000  
25%             95.000000  
50%            283.000000  
75%            365.000000  
90%            365.000000  
99%            365.000000  
max            365.000000

From a rough inspection of the summary statistics, I can see a number of variables that seem to contain outliers. I will analyze the outliers that I'm unsure about further through data visualizations, starting first with number of accommodates and work my way down the list of features that contain outliers.

In [165]:
new_df['price'].iplot(
    kind='hist',
    bins=20,
    xTitle='price',
    linecolor='black',
    yTitle='count',
    title='Price Distribution')

From the above histogram, the majority of listings are a priced under $2500. Listings above this price are definite outliers. 

In [166]:
new_df.iplot(
    x='accommodates',
    y='price',
    xTitle='number of accommodates',
    yTitle='price',
    mode='markers',
    linecolor='black',
    title='Price Versus Number of Accommodates')

In [167]:
new_df['accommodates'].iplot(
    kind='hist',
    bins=20,
    xTitle='number of accommodates',
    linecolor='black',
    yTitle='count',
    title='Distribution of Number of Accommodates')

From the plots above, it looks like the outliers for acommodates are above 10.

Next I will analyze bathrooms.

In [168]:
new_df.iplot(
    x='bathrooms',
    y='price',
    xTitle='number of bathrooms',
    yTitle='price',
    mode='markers',
    linecolor='black',
    title='Price Versus Number of Bathrooms')

In [169]:
new_df['bathrooms'].iplot(
    kind='hist',
    bins=20,
    xTitle='number of bathrooms',
    linecolor='black',
    yTitle='count',
    title='Distribution of Number of Bathrooms')

From the plots above, it looks like the outliers for bathrooms are above 3. 

Next I will analyze bedrooms.

In [170]:
new_df.iplot(
    x='bedrooms',
    y='price',
    xTitle='number of bedrooms',
    yTitle='price',
    mode='markers',
    linecolor='black',
    title='Price Versus Number of Bedrooms')

In [171]:
new_df['bedrooms'].iplot(
    kind='hist',
    bins=20,
    xTitle='number of bedrooms',
    linecolor='black',
    yTitle='count',
    title='Distribution of Number of Bedrooms')

From the plots above, it looks like the outliers for bedrooms are above 4.

Next I will analyze beds.

In [172]:
new_df.iplot(
    x='beds',
    y='price',
    xTitle='number of beds',
    yTitle='price',
    mode='markers',
    linecolor='black',
    title='Price Versus Number of Beds')

In [173]:
new_df['beds'].iplot(
    kind='hist',
    bins=20,
    xTitle='number of beds',
    linecolor='black',
    yTitle='count',
    title='Distribution of Number of Beds')

From the plots above, it looks like the outliers for beds are over 10. 

Next I will analyze bathroom to bedroom ratio.

In [174]:
new_df.iplot(
    x='bedroom_bath_ratio',
    y='price',
    xTitle='bath to bedroom ratio',
    yTitle='price',
    mode='markers',
    linecolor='black',
    title='Price Versus Bath to Bedroom Ratio')

In [175]:
new_df['bedroom_bath_ratio'].iplot(
    kind='hist',
    bins=20,
    xTitle='bath to bedroom ratio',
    linecolor='black',
    yTitle='count',
    title='Distribution of Bath to Bedroom Ratio')

From the plots above, it looks like most listings fall between a 1:2 or 1:1 bathroom to bedroom ratio. 

Next I will inspect records where price is less than the 1th percentile.

In [176]:
# Get subset of dataframe where price is less than 1th percentile and greater than 99th percentile
new_df[(new_df['price'] < new_df['price'].quantile(0.01))].sort_values(by='price')

listing_id  zip_code  latitude  longitude        room_type  \
10626    21838615     78721  30.25990  -97.68495  Entire home/apt   
1655       377391     78704  30.23589  -97.76997  Entire home/apt   
2694     20320755     78704  30.25078  -97.77511  Entire home/apt   
2713     20541331     78704  30.24890  -97.75526     Private room   
2821     21378172     78704  30.25472  -97.77659  Entire home/apt   
...           ...       ...       ...        ...              ...   
6719     21324609     78758  30.38178  -97.70983     Private room   
10561    11492422     78721  30.26732  -97.69239     Private room   
6917     21176341     78744  30.15834  -97.78206     Private room   
6948     24991341     78744  30.15835  -97.78215     Private room   
4606      5702254     78748  30.17370  -97.82393     Private room   

       accommodates  bathrooms  bedrooms  beds  price  minimum_nights  \
10626             8        2.0       3.0   4.0    0.0               5   
1655              2        1.0       1.0   1.0    0.0               1   
2694              6        1.0       2.0   3.0    0.0               2   
2713              2        1.0       1.0   1.0    0.0               3   
2821             10        2.0       4.0   8.0    0.0               3   
...             ...        ...       ...   ...    ...             ...   
6719              2        1.5       1.0   1.0   22.0               2   
10561             2        1.0       1.0   1.0   22.0               7   
6917              1        1.0       1.0   1.0   22.0               2   
6948              2        1.0       1.0   1.0   22.0               2   
4606              1        1.0       1.0   1.0   22.0              31   

       number_of_reviews  review_scores_rating   neighbourhood  \
10626                  5                 100.0       MLK & 183   
1655                   1                 100.0  Travis Heights   
2694                   6                  97.0  Travis Heights   
2713                   2                 100.0  Travis Heights   
2821                  12                 100.0  Travis Heights   
...                  ...                   ...             ...   
6719                  56                  99.0      Gracywoods   
10561                  3                 100.0       MLK & 183   
6917                  22                 100.0        McKinney   
6948                  70                  99.0        McKinney   
4606                   7                 100.0    Cherry Creek   

       number_of_bookings  bedroom_bath_ratio  
10626               362.0           66.666667  
1655                365.0          100.000000  
2694                 18.0           50.000000  
2713                365.0          100.000000  
2821                300.0           50.000000  
...                   ...                 ...  
6719                276.0          150.000000  
10561               365.0          100.000000  
6917                189.0          100.000000  
6948                196.0          100.000000  
4606                 50.0          100.000000  

[109 rows x 16 columns]

There are several listings with a price of \$0. Perhaps this was the price at the time the data scraping occurred and the host changed it soon after (maybe these were new listings). I don't trust these prices so I will remove the 6 records altogether.

In [177]:
# Get subset of data where price is more than 0
new_df = new_df[new_df['price'] > 0]

In [178]:
# Check that the statistics reflects the recent updates of trimming
new_df[['accommodates', 'bathrooms', 'bedrooms', 'beds', 
        'price']].describe(percentiles=[.01, .1, .25, .5, .75, .9, .99])

accommodates     bathrooms      bedrooms          beds         price
count  11333.000000  11333.000000  11333.000000  11333.000000  11333.000000
mean       4.710580      1.550185      1.787258      2.556428    390.907968
std        3.258954      0.892380      1.268425      2.788003   1129.091623
min        1.000000      0.000000      0.000000      0.000000      1.000000
1%         1.000000      1.000000      0.000000      1.000000     23.000000
10%        2.000000      1.000000      1.000000      1.000000     50.000000
25%        2.000000      1.000000      1.000000      1.000000     80.000000
50%        4.000000      1.000000      1.000000      2.000000    145.000000
75%        6.000000      2.000000      2.000000      3.000000    300.000000
90%        8.000000      2.500000      3.000000      5.000000    669.000000
99%       16.000000      5.000000      6.000000     12.000000  10000.000000
max       32.000000     17.000000     23.000000    132.000000  17999.000000

In [179]:
new_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11333 entries, 0 to 11338
Data columns (total 16 columns):
listing_id              11333 non-null int64
zip_code                11333 non-null int64
latitude                11333 non-null float64
longitude               11333 non-null float64
room_type               11333 non-null category
accommodates            11333 non-null int64
bathrooms               11333 non-null float64
bedrooms                11333 non-null float64
beds                    11333 non-null float64
price                   11333 non-null float64
minimum_nights          11333 non-null int64
number_of_reviews       11333 non-null int64
review_scores_rating    11333 non-null float64
neighbourhood           11333 non-null category
number_of_bookings      11333 non-null float64
bedroom_bath_ratio      11333 non-null float64
dtypes: category(2), float64(9), int64(5)
memory usage: 1.3 MB


<b>I will save the cleaned file for easy access. Next step in the process is Exploratory Data Analysis.</b> 

In [180]:
new_df.to_csv('Data/airbnb_clean.csv', index=False)